In [103]:
import json
import plotly.graph_objects as go
from plotly.subplots import make_subplots


import oandapyV20
import oandapyV20.endpoints.positions as positions
import oandapyV20.endpoints.orders as orders
import oandapyV20.endpoints.trades as trades
import oandapyV20.endpoints.pricing as pricing
from oandapyV20.endpoints.accounts import AccountDetails
from oandapyV20.exceptions import V20Error
from oandapyV20.endpoints.instruments import InstrumentsCandles
import numpy as np
import oandapyV20.endpoints.instruments as instruments
import pandas as pd
import os
from dotenv import load_dotenv
from oandapyV20 import API
load_dotenv()

access_token = os.getenv('access_token')
account_id = os.getenv('account_id')
accountID = account_id

client = oandapyV20.API(access_token=access_token, environment="practice")

## Helper Functions


In [32]:

# def get_current_price(instrument):
#     params = {
#         "instruments": instrument
#     }
#     request = pricing.PricingInfo(accountID="101-003-31435840-001", params=params)
#     response = client.request(request)

#     if 'prices' in response and response['prices']:
#         return float(response['prices'][0]['bids'][0]['price'])

#     return None

# def get_instrument_precision(instrument):
#     instrument_precision = {
#         "EUR_USD":4,
#         "AUD_USD":4,
#         "NZD_USD":4,
#         "GBP_USD":4,
#         "GBP_JPY":2,
#         "USD_JPY":2,
#         "EUR_JPY":2
#         }
#     return instrument_precision.get(instrument)  # Set a default precision value if instrument not found


# def get_current_balance():
#     request = AccountDetails(accountID=accountID)
#     response = client.request(request)

#     if response and 'account' in response:
#         account_info = response['account']
#         balance = float(account_info['balance'])
#         return balance


#     return None

# def get_quantity(instrument, trade_direction):
#     current_price = get_current_price(instrument)
#     take_profit_percentage = 0.01  # 1 percent
#     stop_loss_percentage = 0.01    # 1 percent

#     if trade_direction == "BUY":
#         take_profit_price = round(current_price * (1 + take_profit_percentage), get_instrument_precision(instrument))
#         stop_loss_price = round(current_price * (1 - stop_loss_percentage), get_instrument_precision(instrument))
#     elif trade_direction == "SELL":
#         take_profit_price = round(current_price * (1 - take_profit_percentage), get_instrument_precision(instrument))
#         stop_loss_price = round(current_price * (1 + stop_loss_percentage), get_instrument_precision(instrument))
#     else:
#         print("Invalid trade direction")
#         return
#     #print(stop_loss_price, take_profit_price)

#     trade_currency_2 = instrument[4:]
#     position_size=None
#     # A more complex calculation can be done

#     if "USD" in trade_currency_2:
#         position_size = 100000
#     elif "JPY" in trade_currency_2:
#         position_size = 50000
#     else:
#         print("Unsupported currency in the denominator")
#         position_size = None

#     if trade_direction == "BUY":
#         position_size = position_size
#     else:
#         position_size = -position_size

#     return stop_loss_price, take_profit_price, position_size


# def get_open_positions():
#     request = positions.OpenPositions(accountID=account_id)
#     response = client.request(request)
#     open_positions = response.get("positions", [])
#     return open_positions

# def calculate_total_unrealised_pnl(positions_dict):
#     long_pnl = 0
#     short_pnl = 0
#     total_pnl = 0

#     for position in positions_dict:
#         long_unrealized_pnl = float(position['long']['unrealizedPL'])
#         short_unrealized_pnl = float(position['short']['unrealizedPL'])

#         long_pnl += long_unrealized_pnl
#         short_pnl += short_unrealized_pnl
#         total_pnl = long_pnl + short_pnl

#     return long_pnl, short_pnl, total_pnl

# def get_current_balance():
#     request = AccountDetails(accountID=accountID)
#     response = client.request(request)

#     if response and 'account' in response:
#         account_info = response['account']
#         balance = float(account_info['balance'])
#         return balance

# def place_market_order(instrument, units, take_profit_price, stop_loss_price):
#     data = {
#         "order": {
#             "units": str(units),
#             "instrument": instrument,
#             "timeInForce": "FOK",
#             "type": "MARKET",
#             "positionFill": "DEFAULT",
#             "takeProfitOnFill": {
#                 "price": str(float(take_profit_price)),
#             },
#             "stopLossOnFill": {
#                 "price": str(float(stop_loss_price)),
#             }
#         }
#     }

#     try:
#         request = orders.OrderCreate(accountID, data=data)
#         response = client.request(request)
#         print("Oanda Orders placed successfully!")
#     except V20Error as e:
#         print("Error placing Oanda orders:")
#         print(e)



# def close_all_trades(client, account_id):
#     # Get a list of all open trades for the account
#     trades_request = trades.OpenTrades(accountID=account_id)
#     response = client.request(trades_request)

#     if len(response['trades']) > 0:
#         for trade in response['trades']:
#             trade_id = trade['id']
#             try:
#                 # Create a market order to close the trade
#                 data = {
#                     "units": "ALL",
#                 }
#                 order_request = trades.TradeClose(accountID=account_id, tradeID=trade_id, data=data)
#                 response = client.request(order_request)
#                 print(f"Trade {trade_id} closed successfully.")
#             except oandapyV20.exceptions.V20Error as e:
#                 print(f"Failed to close trade {trade_id}. Error: {e}")
#     else:
#         print("No open trades to close.")

# def fetch_candlestick_data(instrument_name, lookback_count):
#     # Initialize the Oanda API client
#     api = API(access_token=access_token, environment="practice")

#     # Define the parameters for the candlestick data request
#     params = {
#         'count': lookback_count,
#         'granularity': 'H1',
#         'price': 'M',  # Midpoint candlestick prices
#     }

#     # Request the candlestick data from Oanda API
#     candles_request = InstrumentsCandles(instrument=instrument_name, params=params)
#     response = api.request(candles_request)

#     # Extract the close prices from the response
#     timestamps = [candle['time'] for candle in response['candles']] # I add this in case needed
#     close_prices = [float(candle['mid']['c']) for candle in response['candles']]

#     return pd.Series(data=close_prices, index=pd.to_datetime(timestamps), name=instrument_name)

# def generate_signal(instrument_name, lookback_count, stma_period, ltma_period):
#     # Fetch candlestick data
#     close_prices = fetch_candlestick_data(instrument_name, lookback_count)

#     # Calculate short-term moving average (STMA)
#     stma = np.mean(close_prices[-stma_period:])

#     # Calculate long-term moving average (LTMA)
#     ltma = np.mean(close_prices[-ltma_period:])

#     # Check for crossover
#     if stma > ltma:
#         signal = "BUY"
#     else:
#         signal = "SELL"

#     return signal

## Choose Trading Pairs:
1. the best n pairs with the highest approximated liquidies
2. and they do not have too extreme volatility

In [33]:
# import random
# import pytz

# # === Parameters ===
# usd_pairs = [
#     'EUR_USD', 'USD_JPY', 'GBP_USD', 'USD_CHF', 'USD_CAD', 'AUD_USD', 'NZD_USD',
#     'USD_HKD', 'USD_SGD', 'USD_SEK', 'USD_NOK', 'USD_DKK', 'USD_ZAR', 'USD_THB',
#     'USD_MXN', 'USD_CNH', 'USD_TRY', 'USD_INR', 'USD_PLN', 'USD_HUF', 'USD_CZK'
# ]
# granularity = 'M1'

# # === Generate 5 random weekdays from last 3 years ===
# def get_random_weekdays(n_days, years_back=3):
#     end_date = datetime.datetime.utcnow().date()
#     start_date = end_date - datetime.timedelta(days=365 * years_back)
#     possible_dates = pd.bdate_range(start=start_date, end=end_date, freq='C')
#     return random.sample(list(possible_dates), n_days)

# random_dates = get_random_weekdays(5)
# print("Selected Random Dates:")
# for d in random_dates:
#     print(d)

# # === Fetch M1 data for specific date ===
# def fetch_day_candles(pair, date):
#     # start = datetime.datetime.combine(date, datetime.time(0, 0)).strftime('%Y-%m-%dT%H:%M:%SZ')
#     # end = datetime.datetime.combine(date, datetime.time(23, 59)).strftime('%Y-%m-%dT%H:%M:%SZ')
#     start = datetime.datetime.combine(date, datetime.time(10, 0)).strftime('%Y-%m-%dT%H:%M:%SZ')
#     end = datetime.datetime.combine(date, datetime.time(13, 0)).strftime('%Y-%m-%dT%H:%M:%SZ')
#     params = {
#         "granularity": granularity,
#         "price": "M",
#         "from": start,
#         "to": end
#     }
#     r = instruments.InstrumentsCandles(instrument=pair, params=params)
#     client.request(r)
#     return r.response['candles']

# # === Fetch 1 year recent candles for volatility ===
# def fetch_year_candles(pair):
#     all_candles = []
#     end_time = datetime.datetime.utcnow()
#     count_needed = 365 * 1440
#     max_per_request = 5000

#     while count_needed > 0:
#         count = min(count_needed, max_per_request)
#         params = {
#             "granularity": granularity,
#             "count": count,
#             "price": "M",
#             "to": end_time.strftime('%Y-%m-%dT%H:%M:%SZ')
#         }
#         r = instruments.InstrumentsCandles(instrument=pair, params=params)
#         client.request(r)
#         candles = r.response['candles']
#         if not candles:
#             break
#         all_candles = candles + all_candles
#         end_time = datetime.datetime.fromisoformat(candles[0]['time'][:-1])
#         count_needed -= len(candles)
#         time.sleep(0.15)
#     return all_candles

# # === Main Calculation ===
# results = []

# for pair in usd_pairs:
#     print(f"Processing {pair}...")
#     try:
#         # 1. spread （only approximation)
#         spread_list = []
#         for date in random_dates:
#             candles = fetch_day_candles(pair, date)
#             if len(candles) < 100:
#                 continue
#             highs = np.array([float(c['mid']['h']) for c in candles])
#             lows = np.array([float(c['mid']['l']) for c in candles])
#             spreads = highs - lows
#             spread_list.append(np.mean(spreads))
#             time.sleep(0.15)

#         if len(spread_list) < 3:
#             print(f"Skipping {pair} due to insufficient spread data")
#             continue
#         avg_spread = np.mean(spread_list)

#         # 2. volatility
#         year_candles = fetch_year_candles(pair)
#         closes = np.array([float(c['mid']['c']) for c in year_candles])
#         if len(closes) < 1000:
#             print(f"Skipping {pair} due to insufficient volatility data")
#             continue
#         log_returns = np.diff(np.log(closes))
#         volatility = np.std(log_returns) * np.sqrt(252 * 1440)

#         # 3. Save result
#         results.append({
#             'pair': pair,
#             'average_spread': avg_spread,
#             'volatility': volatility
#         })

#     except Exception as e:
#         print(f"Error processing {pair}: {e}")

# # === Ranking and Filtering ===
# df = pd.DataFrame(results)
# df['liquidity_rank'] = df['average_spread'].rank(method='min')
# df['volatility_rank'] = df['volatility'].rank(ascending=False, method='min')
# df = df.sort_values(by='liquidity_rank')

# filtered = df[(df['liquidity_rank'] <= 5) & (df['volatility_rank'] > 5)]
# print("\n=== Recommended Pairs for Strategy Development ===")
# print(filtered[['pair', 'average_spread', 'liquidity_rank', 'volatility', 'volatility_rank']])

In [34]:
# df

In [35]:
# df[(df['liquidity_rank'] <= 5) & (df['volatility_rank'] > 5)]["pair"]

## Data for Designing the Trading Strategy

In [36]:
# chosen_pairs = ["USD_HKD", "NZD_USD", "AUD_USD", "USD_CHF", "USD_SGD"] #list(df[(df['liquidity_rank'] <= 5) & (df['volatility_rank'] > 5)]["pair"])
# data = {pair: fetch_candlestick_data(pair, lookback_count=200) for pair in chosen_pairs} # past 200 days, hourly data
# df = pd.DataFrame(data)
# df = df[chosen_pairs]
# df


In [ ]:
import pandas as pd
from datetime import datetime

forex_pairs = ["USD_HKD", "NZD_USD", "AUD_USD", "USD_CHF", "USD_SGD"]
benchmark_symbol = "EUR_USD"

start_date = '2015-01-01'
end_date = '2024-12-31'
initial_balance = 10000

def fetch_daily_data(instrument, start_date, end_date, granularity='D'):
    from oandapyV20 import API
    from oandapyV20.endpoints.instruments import InstrumentsCandles
    import pandas as pd
    # Convert dates to ISO format
    start_iso = pd.to_datetime(start_date).isoformat("T") + "Z"
    end_iso = pd.to_datetime(end_date).isoformat("T") + "Z"
    params = {
        "from": start_iso,
        "to": end_iso,
        "granularity": granularity,  # Daily data
        "price": "M"  # Use midpoint prices
    }
    # Replace with your OANDA API access token
    client = API(access_token=access_token, environment="practice")
    r = InstrumentsCandles(instrument=instrument, params=params)
    response = client.request(r)
    candles = response.get("candles", [])
    dates = []
    closes = []
    for candle in candles:
        if candle.get("complete", False):
            dates.append(pd.to_datetime(candle["time"]))
            closes.append(float(candle["mid"]["c"]))
    series = pd.Series(closes, index=dates, name=instrument)
    series = series.sort_index()
    return series

# Fetch daily closing price data for each forex pair
data_dict = {}
for inst in forex_pairs:
    data_dict[inst] = fetch_daily_data(inst, start_date, end_date, granularity='D')

# If benchmark_symbol is not in forex_pairs, fetch benchmark data separately
benchmark_series = fetch_daily_data(benchmark_symbol, start_date, end_date, granularity='D')

# Combine all forex pair data into a single DataFrame (columns are forex pairs)
df_close = pd.DataFrame(data_dict)

# Create a MultiIndex DataFrame: first level is 'Close', second level is forex pair names
multi_columns = pd.MultiIndex.from_product([["Close"], df_close.columns])
forex_data = pd.DataFrame(df_close.values, index=df_close.index, columns=multi_columns)

benchmark_data = benchmark_series


In [38]:
print(forex_data.head())
print(benchmark_data.head())

                             Close                                    
                           USD_HKD  NZD_USD  AUD_USD  USD_CHF  USD_SGD
2015-01-01 22:00:00+00:00  7.75651  0.76998  0.80894  1.00163  1.33132
2015-01-04 22:00:00+00:00  7.75593  0.76856  0.80830  1.00700  1.33532
2015-01-05 22:00:00+00:00  7.75430  0.77624  0.80844  1.01010  1.33323
2015-01-06 22:00:00+00:00  7.75490  0.77844  0.80790  1.01432  1.33838
2015-01-07 22:00:00+00:00  7.75448  0.78242  0.81231  1.01836  1.33671
2015-01-01 22:00:00+00:00    1.20020
2015-01-04 22:00:00+00:00    1.19324
2015-01-05 22:00:00+00:00    1.18902
2015-01-06 22:00:00+00:00    1.18392
2015-01-07 22:00:00+00:00    1.17927
Name: EUR_USD, dtype: float64


In [70]:
#!/usr/bin/env python
import warnings
import itertools
import numpy as np
import pandas as pd
# Forex strategies may use Plotly for visualization (you may choose another library if needed)
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import plotly.express as px
import statsmodels.api as sm

import plotly.io as pio

import empyrical as ep
import requests
import re
from bs4 import BeautifulSoup
import multiprocessing
from tqdm import tqdm

from datetime import datetime

warnings.filterwarnings("ignore")
pd.set_option('display.max_columns', 1000)
pd.set_option('display.max_rows', 1000)
pd.set_option('display.width', 1000)
pd.set_option('display.max_colwidth', 1000)

pio.renderers.default = "notebook+pdf"  # Set the renderer based on your environment

# ----------------------------- Helper Functions ----------------------------- #
def calculate_ratios(series, risk_free_rate=0.0):
    daily_returns = series.pct_change().dropna()
    
    # Sharpe Ratio
    sharpe_ratio = (daily_returns.mean() / daily_returns.std()) * np.sqrt(252)

    # Annualized Return
    cumulative_return = series.iloc[-1] / series.iloc[0] - 1
    num_years = len(series) / 252
    annualized_return = (1 + cumulative_return) ** (1 / num_years) - 1

    # Annualized Volatility
    annualized_volatility = daily_returns.std() * np.sqrt(252)

    # Maximum Drawdown
    rolling_max = series.cummax()
    drawdown = series / rolling_max - 1
    max_drawdown = drawdown.min()

    # Calmar Ratio
    calmar_ratio = -annualized_return / max_drawdown if max_drawdown != 0 else np.nan

    # Sortino Ratio
    downside_returns = daily_returns[daily_returns < 0]
    downside_volatility = downside_returns.std() * np.sqrt(252)
    sortino_ratio = (annualized_return - risk_free_rate) / downside_volatility if downside_volatility != 0 else np.nan

    return {
        'Sharpe Ratio': sharpe_ratio,
        'Annualized Return': annualized_return,
        'Annualized Volatility': annualized_volatility,
        'Final Accumulated Profit': series.iloc[-1] - initial_balance,  # Note: initial_balance must be defined externally
        'Maximum Drawdown': max_drawdown,
        'Calmar Ratio': calmar_ratio,
        'Sortino Ratio': sortino_ratio,
    }

def calculate_beta(asset_returns, benchmark_data):
    benchmark_returns = benchmark_data.pct_change().dropna()

    asset_returns, benchmark_returns = asset_returns.align(benchmark_returns, join='inner')
    covariance = np.cov(asset_returns, benchmark_returns)[0][1]
    benchmark_variance = np.var(benchmark_returns.loc[asset_returns.index])
    beta = covariance / benchmark_variance
    return beta

def information_ratio(returns):
    benchmark_returns = np.zeros(len(returns))
    tracking_error = np.std(returns - benchmark_returns)
    return (returns.mean() - benchmark_returns.mean()) / tracking_error if tracking_error != 0 else np.nan

# The functions below (get_htm_links, extract_date_from_url, match_cpi_with_report_date, get_cpi_data_from_fred, get_cpi_df, merge_data_with_cpi)
# were originally used to obtain CPI data. If CPI factors are not needed for your forex strategy, you may ignore these functions.

# ----------------------------- TradingStrategy Class ----------------------------- #
class TradingStrategy:
    def __init__(self, instruments, data, benchmark_data, short_window=20, long_window=30,
                 stop_loss_percentage=1, rsi_period=30, initial_balance=10000, rsi_weight_param=1, use_cpi=False, cpi_cutoff=2.5, cpi_delay=2):
        """
        Initialize the trading strategy.
        For forex strategies, 'instruments' is a list of currency pairs, 'data' is a MultiIndex DataFrame
        containing historical price data (with 'Close' prices), and benchmark_data can be set to a benchmark forex pair or exchange rate index.
        """
        self.instruments = instruments  # List of forex currency pairs (e.g., ['EUR_USD', 'GBP_USD', ...])
        self.data = data                # Data should be a MultiIndex DataFrame; first level is the instrument, second level contains 'Close'
        self.original_data = data.copy()  # Save a backup of the original data
        self.benchmark_data = benchmark_data
        self.short_window = short_window
        self.long_window = long_window
        self.stop_loss_percentage = stop_loss_percentage
        self.rsi_period = rsi_period
        self.initial_balance = initial_balance
        self.rsi_weight_param = rsi_weight_param
        self.use_cpi = use_cpi
        self.cpi_cutoff = cpi_cutoff
        self.cpi_delay = cpi_delay

    def calculate_rsi(self, data, period=14):
        delta = data.diff()
        gain = delta.where(delta > 0, 0)
        loss = -delta.where(delta < 0, 0)
        avg_gain = gain.rolling(window=period).mean()
        avg_loss = loss.rolling(window=period).mean()
        rs = avg_gain / avg_loss
        rsi = 100 - (100 / (1 + rs))
        return rsi

    def calculate_ema(self, data, span):
        return data.ewm(span=span, adjust=False).mean()

    # Backtesting for a single currency pair (applicable to forex data)
    def strategy(self):
        """
        Backtest the strategy for each currency pair to generate buy/sell signals,
        positions, and cumulative profit curves.
        Assumes that self.data is a MultiIndex DataFrame where the first level contains the instrument names
        and the second level contains at least the 'Close' price data.
        """
        instrument_series = {}
        trades = {inst: {'buy_dates': [], 'buy_prices': [], 'sell_dates': [], 'sell_prices': []} 
                  for inst in self.instruments}
        cash = self.initial_balance
        
        for inst in self.instruments:
            # Calculate technical indicators
            self.data[(inst, f'{self.short_window}_SMA')] = self.data['Close'][inst].rolling(window=self.short_window).mean()
            self.data[(inst, f'{self.long_window}_SMA')] = self.data['Close'][inst].rolling(window=self.long_window).mean()
            self.data[(inst, 'RSI')] = self.calculate_rsi(self.data['Close'][inst], period=self.rsi_period)
            self.data[(inst, f'{self.short_window}_EMA')] = self.calculate_ema(self.data['Close'][inst], span=self.short_window)
            self.data[(inst, 'Close')] = self.data['Close'][inst]
            self.data[(inst, 'Signal')] = 0

            # Define base buy signal condition
            buy_condition_base = (
                (self.data[(inst, f'{self.short_window}_SMA')] > self.data[(inst, f'{self.long_window}_SMA')]) &
                (self.data[(inst, 'RSI')] < 70) &
                (self.data[(inst, 'Close')] > self.data[(inst, f'{self.short_window}_EMA')])
            )

            if self.use_cpi:
                same_day_buy_condition = buy_condition_base & (self.data[(inst, 'CPI_change')] < self.cpi_cutoff)
                delayed_buy_condition = (buy_condition_base & (self.data[(inst, 'CPI_change')] >= self.cpi_cutoff)).shift(self.cpi_delay)
                buy_condition = same_day_buy_condition | delayed_buy_condition
            else:
                buy_condition = buy_condition_base
            self.data.loc[buy_condition, (inst, 'Signal')] = 1
            sell_condition = ((self.data[(inst, f'{self.short_window}_SMA')] < self.data[(inst, f'{self.long_window}_SMA')]) |
                              (self.data[(inst, 'RSI')] > 70))
            self.data.loc[sell_condition, (inst, 'Signal')] = -1

            # Backtesting process for each currency pair
            position = 0
            entry_price = 0
            stop_loss_price = 0
            accumulated_profit = self.initial_balance
            profit_history = []
            
            buy_dates = []
            sell_dates = []
            buy_prices = []
            sell_prices = []

            # Start backtesting from the index corresponding to long_window
            for i in range(self.long_window, len(self.data)):
                current_date = self.data.index[i]
                current_price = self.data[(inst, 'Close')].iloc[i]
                signal = self.data[(inst, 'Signal')].iloc[i]

                if signal == 1 and position == 0 and cash > 0:
                    position = 1
                    entry_price = current_price
                    # For forex strategies, we use full available funds to buy, determining the position size
                    units = cash / current_price   # Number of units purchased
                    cash = 0                        # All funds are used
                    stop_loss_price = entry_price * (1 - self.stop_loss_percentage / 100)
                    buy_dates.append(current_date)
                    buy_prices.append(entry_price)

                elif position == 1:
                    # If the current price falls below the stop-loss or a sell signal is triggered, then close the position
                    if (current_price <= stop_loss_price) or (signal == -1):
                        position = 0
                        sell_dates.append(current_date)
                        sell_prices.append(current_price)
                        profit = units * (current_price - entry_price)
                        accumulated_profit += profit
                        cash += units * current_price  # Funds are returned after closing
                        units = 0

                profit_history.append(accumulated_profit)

            # If a position is still open, close it using the final price
            if position == 1:
                current_price = self.data[(inst, 'Close')].iloc[-1]
                current_date = self.data.index[-1]
                sell_dates.append(current_date)
                sell_prices.append(current_price)
                profit = units * (current_price - entry_price)
                accumulated_profit += profit
                cash += units * current_price
                profit_history[-1] = accumulated_profit

            trades[inst]['buy_dates'] = buy_dates
            trades[inst]['sell_dates'] = sell_dates
            trades[inst]['buy_prices'] = buy_prices
            trades[inst]['sell_prices'] = sell_prices

            # Save the cumulative profit series (backtesting results)
            instrument_series[inst] = pd.Series(profit_history, index=self.data.index[self.long_window:])

        return instrument_series, trades

    # Backtesting for the portfolio strategy
    def portfolio_strategy(self):
        """
        Backtest the portfolio strategy. Assume that each day the currency pairs generating a buy signal
        are selected, and funds are allocated according to RSI weights.
        """
        self.strategy()  # First, calculate the signals for each currency pair
        cash = self.initial_balance
        positions = {inst: None for inst in self.instruments}  # Record the position for each currency pair
        trades = {inst: {'buy_dates': [], 'buy_prices': [], 'sell_dates': [], 'sell_prices': []} for inst in self.instruments}
        portfolio_history = []
        portfolio_states = []

        for current_date in self.data.index[self.long_window:]:
           
            # Check if the positions already held trigger a closing condition
            for inst in self.instruments:
                if positions[inst] is not None:
                    current_price = self.data[(inst, 'Close')].loc[current_date]
                    current_signal = self.data[(inst, 'Signal')].loc[current_date]
                    entry_price = positions[inst]['entry_price']
                    stop_loss_price = positions[inst]['stop_loss']
                    if (current_signal == -1) or (current_price <= stop_loss_price):
                        shares = positions[inst]['units']
                        cash += shares * current_price
                        trades[inst]['sell_dates'].append(current_date)
                        trades[inst]['sell_prices'].append(current_price)
                        positions[inst] = None

            # Select currency pairs with a buy signal that are not in a current position
            buy_candidates = []
            for inst in self.instruments:
                if positions[inst] is None:
                    current_signal = self.data[(inst, 'Signal')].loc[current_date]
                    if current_signal == 1:
                        current_price = self.data[(inst, 'Close')].loc[current_date]
                        current_rsi = self.data[(inst, 'RSI')].loc[current_date]
                        weight = max(70 - current_rsi, 0) ** self.rsi_weight_param
                        if weight > 0:
                            buy_candidates.append((inst, current_price, current_rsi, weight))
            if buy_candidates and cash > 0:
                total_weight = sum([cand[3] for cand in buy_candidates])
                for cand in buy_candidates:
                    inst, price, current_rsi, weight = cand
                    allocation = cash * (weight / total_weight)
                    units_to_buy = allocation / price  # Units to buy (can be fractional)
                    if units_to_buy > 0:
                        cost = units_to_buy * price
                        cash -= cost
                        stop_loss_price = price * (1 - self.stop_loss_percentage / 100)
                        positions[inst] = {'entry_price': price, 'units': units_to_buy, 'stop_loss': stop_loss_price}
                        trades[inst]['buy_dates'].append(current_date)
                        trades[inst]['buy_prices'].append(price)

            current_units = {inst: (positions[inst]['units'] if positions[inst] is not None else 0) for inst in self.instruments}
            portfolio_states.append({'date': current_date, 'cash': cash, **current_units})
            
            total_value = cash
            for inst in self.instruments:
                if positions[inst] is not None:
                    current_price = self.data[(inst, 'Close')].loc[current_date]
                    total_value += positions[inst]['units'] * current_price
            portfolio_history.append((current_date, total_value))

        # Finally, close all open positions
        last_date = self.data.index[-1]
        for inst in self.instruments:
            if positions[inst] is not None:
                current_price = self.data[(inst, 'Close')].loc[last_date]
                cash += positions[inst]['units'] * current_price
                trades[inst]['sell_dates'].append(last_date)
                trades[inst]['sell_prices'].append(current_price)
                positions[inst] = None
        portfolio_history.append((last_date, cash))
        portfolio_series = {'portfolio': pd.Series(data=[val for date, val in portfolio_history],
                                                    index=[date for date, val in portfolio_history])}
        
        portfolio_states_df = pd.DataFrame(portfolio_states).set_index('date')
        portfolio_states_df = portfolio_states_df.reindex(self.data.index[self.long_window:], method='ffill')
        trades['state'] = portfolio_states_df
        
        return portfolio_series, trades

    # Calculate performance metrics
    def backtest(self, series):
        performance_metrics = {}
        for inst, series in series.items():
            returns = series.pct_change().fillna(0)
            accumulated_profit = series.iloc[-1] - series.iloc[0]
            metrics = calculate_ratios(series)
            metrics.update({
                'Final Accumulated Profit': accumulated_profit,
                'Treynor Ratio': calculate_beta(returns, self.benchmark_data),
                'Information Ratio': information_ratio(returns)
            })
            performance_metrics[inst] = metrics
        return performance_metrics

    def backtest_portfolio(self):
        portfolio_series, trades = self.portfolio_strategy()
        return self.backtest(portfolio_series), trades

    def backtest_instruments(self):
        instrument_series, trades = self.strategy()
        return self.backtest(instrument_series), trades

    def plot_returns_comparison(self):
        instrument_series, instrument_trades = self.strategy()  
        portfolio_series, portfolio_trades = self.portfolio_strategy()
        
        start_index = self.data.index[self.long_window:]
        
        cumulative_instrument_returns = {}
        cumulative_strategy_returns = {}
        for inst, series in instrument_series.items():
            temp_prices = self.data['Close'][inst].loc[start_index]
            temp_returns = temp_prices.pct_change().fillna(0)
            cumulative_instrument_returns[inst] = (1 + temp_returns).cumprod() - 1
            
            temp_strategy_returns = series.pct_change().fillna(0)
            cumulative_strategy_returns[inst] = (1 + temp_strategy_returns).cumprod() - 1
        
        portfolio_daily_returns = portfolio_series['portfolio'].pct_change().fillna(0)
        cumulative_portfolio = (1 + portfolio_daily_returns).cumprod() - 1
        benchmark_prices = self.benchmark_data.reindex(start_index, method='ffill')
        
        benchmark_returns = benchmark_prices.pct_change().fillna(0)
        cumulative_benchmark = (1 + benchmark_returns).cumprod() - 1
        
        fig = go.Figure()
        for inst in self.instruments:
            fig.add_trace(go.Scatter(
                x=cumulative_strategy_returns[inst].index,
                y=cumulative_strategy_returns[inst],
                mode='lines',
                name=f'{inst} Strategy Returns'
            ))
            fig.add_trace(go.Scatter(
                x=cumulative_instrument_returns[inst].index,
                y=cumulative_instrument_returns[inst],
                mode='lines',
                name=f'{inst} Raw Returns',
                line=dict(dash='dot')
            ))
            buy_dates = [d for d in instrument_trades[inst]['buy_dates'] if d in start_index]
            buy_values = cumulative_strategy_returns[inst].loc[buy_dates]
            fig.add_trace(go.Scatter(
                x=buy_dates,
                y=buy_values,
                mode='markers',
                name=f'{inst} Buy',
                marker=dict(symbol='triangle-up', color='green', size=10)
            ))
            sell_dates = [d for d in instrument_trades[inst]['sell_dates'] if d in start_index]
            sell_values = cumulative_strategy_returns[inst].loc[sell_dates]
            fig.add_trace(go.Scatter(
                x=sell_dates,
                y=sell_values,
                mode='markers',
                name=f'{inst} Sell',
                marker=dict(symbol='triangle-down', color='red', size=10)
            ))
        
        fig.add_trace(go.Scatter(
            x=cumulative_portfolio.index,
            y=cumulative_portfolio,
            mode='lines',
            name='Portfolio Returns',
            line=dict(width=3, color='blue')
        ))
        
        fig.add_trace(go.Scatter(
            x=cumulative_benchmark.index,
            y=cumulative_benchmark,
            mode='lines',
            name='Benchmark Returns',
            line=dict(width=3, color='orange')
        ))
        
        fig.update_layout(
            title='Forex Trading Strategy: Instruments, Portfolio & Benchmark',
            xaxis_title='Date',
            yaxis_title='Cumulative Returns',
            template='plotly_dark',
            legend_title='Legend',
            legend=dict(x=1.02, y=1, xanchor='left', yanchor='top'),
            width=1400, height=600
        )
        
        # fig.write_image("trading_strategy.png", engine="kaleido")
        fig.show()
        

    # Tuning and parameter optimization functions remain basically unchanged and can be adjusted as needed
    def backtest_tune(self, series):
        performance_metrics = {}
        for inst, series in series.items():
            returns = series.pct_change().fillna(0)
            accumulated_profit = series.iloc[-1] - series.iloc[0]
            performance_metrics[inst] = {
                'Sharpe Ratio': calculate_ratios(series)['Sharpe Ratio'],
                'Annualized Return': calculate_ratios(series)['Annualized Return'],
                'Annualized Volatility': calculate_ratios(series)['Annualized Volatility'],
                'Final Accumulated Profit': accumulated_profit,
                'Maximum Drawdown': calculate_ratios(series)['Maximum Drawdown'],
                'Calmar Ratio': calculate_ratios(series)['Calmar Ratio'],
                'Sortino Ratio': calculate_ratios(series)['Sortino Ratio'],
                'Treynor Ratio': calculate_beta(returns, self.benchmark_data),
                'Information Ratio': information_ratio(returns),
            }
        return performance_metrics

    def tune_parameters(
                self, 
                ratio='Sharpe Ratio', 
                tune_rsi=True,
                train_start=None,    
                train_end=None,      
                test_start=None,     
                test_end=None       
            ):
     
        # train_data = self.original_data.loc[train_start:train_end].copy()
        # test_data = self.original_data.loc[test_start:test_end].copy()

        short_window_range = range(10, 40, 10)
        long_window_range = range(20, 50, 5)
        stop_loss_range = range(1, 11, 2)
        rsi_period_range = range(10, 35, 5)
        # short_window_range = range(10, 20, 10)
        # long_window_range = range(20, 25, 5)
        # stop_loss_range = range(1, 10, 2)
        # rsi_period_range = range(10, 15, 5)

        if tune_rsi:
            rsi_weight_range = np.linspace(0.5, 1.5, 11)
            param_combinations = itertools.product(
                short_window_range, 
                long_window_range, 
                stop_loss_range, 
                rsi_period_range, 
                rsi_weight_range
            )
        else:
            param_combinations = itertools.product(
                short_window_range, 
                long_window_range, 
                stop_loss_range, 
                rsi_period_range
            )

        best_params = None
        best_ratio = -np.inf
        all_results = []

        for params in tqdm(param_combinations, desc="Tuning Parameters"):
        
            self.data = self.original_data.loc[train_start:train_end].copy()

            if tune_rsi:
                short_window, long_window, stop_loss_percentage, rsi_period, rsi_weight_param = params
                self.rsi_weight_param = rsi_weight_param
            else:
                short_window, long_window, stop_loss_percentage, rsi_period = params
            
          
            if short_window >= long_window:
                continue
            
      
            self.short_window = short_window
            self.long_window = long_window
            self.stop_loss_percentage = stop_loss_percentage
            self.rsi_period = rsi_period

            
            performance_metrics, _ = self.backtest_portfolio()

   
            avg_ratio = np.mean([m[ratio] for m in performance_metrics.values()])

           
            param_result = {
                'short_window': short_window,
                'long_window': long_window,
                'stop_loss_percentage': stop_loss_percentage,
                'rsi_period': rsi_period,
                ratio: avg_ratio
            }
            if tune_rsi:
                param_result['rsi_weight_param'] = rsi_weight_param

            all_results.append(param_result)

       
            if avg_ratio > best_ratio:
                best_ratio = avg_ratio
                best_params = param_result

    
      
        # self.data = self.original_data.loc[train_start:train_end].copy()
        # self.short_window = best_params['short_window']
        # self.long_window = best_params['long_window']
        # self.stop_loss_percentage = best_params['stop_loss_percentage']
        # self.rsi_period = best_params['rsi_period']
        # if tune_rsi:
        #     self.rsi_weight_param = best_params['rsi_weight_param']

        # final_train_perf, _ = self.backtest_portfolio()
      
        # final_train_metrics = {}
        # if 'portfolio' in final_train_perf:
        #     final_train_metrics = final_train_perf['portfolio']
        # else:
           
        #     final_train_metrics = {
        #         'Return': np.mean([m['Annualized Return'] for m in final_train_perf.values()]),
        #         'Sharpe': np.mean([m['Sharpe Ratio'] for m in final_train_perf.values()]),
        #         'MaxDrawdown': np.mean([m['Maximum Drawdown'] for m in final_train_perf.values()]),
              
        #     }

    
        # self.data = self.original_data.loc[test_start:test_end].copy()
     
        # final_test_perf, _ = self.backtest_portfolio()
        # final_test_metrics = {}
        # if 'portfolio' in final_test_perf:
        #     final_test_metrics = final_test_perf['portfolio']
        # else:
        #     final_test_metrics = {
        #         'Return': np.mean([m['Annualized Return'] for m in final_test_perf.values()]),
        #         'Sharpe': np.mean([m['Sharpe Ratio'] for m in final_test_perf.values()]),
        #         'MaxDrawdown': np.mean([m['Maximum Drawdown'] for m in final_test_perf.values()]),
        #     }

        return best_params, best_ratio, all_results #, final_train_metrics, final_test_metrics


In [49]:
strategy = TradingStrategy(
    forex_pairs, data=forex_data, benchmark_data=benchmark_data,
    short_window=10, long_window=20,
    stop_loss_percentage=5, rsi_period=30,
    initial_balance=initial_balance, rsi_weight_param=1.5
)

# _,_ = strategy.backtest_stock()
performance_metrics,_ =strategy.backtest_portfolio()
# Plot the cumulative returns of the portfolio and benchmark
strategy.plot_returns_comparison()

In [71]:
train_start = "2019-01-01"
train_end   = "2023-12-31"
test_start  = "2024-01-01"
test_end    = "2024-12-31"

optimized_strategy = TradingStrategy(
    forex_pairs, data=forex_data, benchmark_data=benchmark_data,
    short_window=20, long_window=40,
    stop_loss_percentage=5, rsi_period=30,
    initial_balance=initial_balance, rsi_weight_param=1.5
)

best_params, best_ratio, all_results = optimized_strategy.tune_parameters(
    ratio="Sharpe Ratio",
    tune_rsi=True,
    train_start=train_start,
    train_end=train_end,
    test_start=test_start,
    test_end=test_end
)



Tuning Parameters: 4950it [36:56,  2.23it/s] 


In [ ]:
# pd.DataFrame(all_results).to_json("tuning_results.json", orient="records", lines=True)

In [76]:
pd.DataFrame(all_results).sort_values(by="Sharpe Ratio", ascending=False).head(10)


short_window  long_window  stop_loss_percentage  rsi_period  Sharpe Ratio  rsi_weight_param
2829            20           45                     3          20      0.719636               0.7
2831            20           45                     3          20      0.709623               0.9
648             10           30                     3          25      0.691193               1.5
813             10           30                     9          25      0.691193               1.5
758             10           30                     7          25      0.691193               1.5
703             10           30                     5          25      0.691193               1.5
56              10           20                     3          10      0.689354               0.6
812             10           30                     9          25      0.686681               1.4
647             10           30                     3          25      0.686681               1.4
757             10           30                     7          25      0.686681               1.4

In [120]:
with open("tuning_results.json", "r") as f:
    result_data = [json.loads(line) for line in f]  # Load each line as a JSON object
df = pd.DataFrame(result_data)
best_params = df.sort_values(by="Sharpe Ratio", ascending=False).head(1).iloc[0].to_dict()

# Exclude "Sharpe Ratio" from the list of tunable parameters
params = [p for p in best_params if p != "Sharpe Ratio"]

# Create a 2x3 grid of subplots
rows = 2
cols = 3
fig = make_subplots(rows=rows, cols=cols,
                    subplot_titles=[f"{p} vs Sharpe Ratio Distribution" for p in params])

# Loop through each parameter
for idx, param in enumerate(params):
    row = idx // cols + 1
    col = idx % cols + 1

    # Convert parameter values to string so Plotly treats them as categories
    df[param] = df[param].astype(str)

    # Draw a boxplot for each unique parameter value
    for val in sorted(df[param].unique(), key=lambda x: float(x)):
        val_df = df[df[param] == val]
        fig.add_trace(
            go.Box(
                y=val_df["Sharpe Ratio"],
                name=val,
                boxpoints="all",   # Show all points
                jitter=0.3,        # Add jitter to scatter points
                pointpos=-1.8,     # Position of scatter points
                marker=dict(size=3),
                showlegend=False,

            ),
            row=row, col=col
        )

    # Add a red dashed vertical line for the best parameter value
    for p in best_params.keys():
        if p != "Sharpe Ratio" and p !="rsi_weight_param":
            best_params[p] = int(best_params[p])
    

    best_val_str = str(best_params[param])
    fig.add_trace(
        go.Scatter(
            x=[best_val_str, best_val_str],
            y=[df["Sharpe Ratio"].min(), df["Sharpe Ratio"].max()],
            mode="lines",
            line=dict(color="red", dash="dash"),
            name=f"Best {param}",
            showlegend=(idx == 0)  # Only show legend once
        ),
        row=row, col=col
    )

# Final plot settings
fig.update_layout(
    height=900,
    width=1400,
    title_text="Sharpe Ratio Distributions by Parameter",
    showlegend=True
)

# Display the figure
fig.show()

In [118]:
best_val_str

'0.7'

In [90]:
strategy_train = TradingStrategy(
    forex_pairs, data=forex_data[train_start:train_end], benchmark_data=benchmark_data,
    short_window=best_params['short_window'], long_window=best_params['long_window'],
    stop_loss_percentage=best_params['stop_loss_percentage'], rsi_period=best_params['rsi_period'],
    initial_balance=initial_balance, rsi_weight_param=best_params['rsi_weight_param'],
)

In [88]:
strategy_test = TradingStrategy(
    forex_pairs, data=forex_data[test_start:test_end], benchmark_data=benchmark_data,
    short_window=best_params['short_window'], long_window=best_params['long_window'],
    stop_loss_percentage=best_params['stop_loss_percentage'], rsi_period=best_params['rsi_period'],
    initial_balance=initial_balance, rsi_weight_param=best_params['rsi_weight_param'],
)

# _,_ = strategy.backtest_stock()
performance_metrics,_ = strategy_test.backtest_portfolio()
# Plot the cumulative returns of the portfolio and benchmark
# strategy.plot_returns_comparison()
pd.DataFrame(performance_metrics)

portfolio
Sharpe Ratio               0.061876
Annualized Return          0.001909
Annualized Volatility      0.058249
Final Accumulated Profit  16.363619
Maximum Drawdown          -0.059940
Calmar Ratio               0.031854
Sortino Ratio              0.042454
Treynor Ratio             -0.092640
Information Ratio          0.003898

In [ ]:
# ----------------------------------- Visualization Input ---------------------------------- #
"""
Input: 
    - portfolio_series: A [dictionary] containing the portfolio series for each pair/ the portfolio
    - trades: A [dictionary] containing the trades for each pair
        - buy_dates: A [list] of buy dates for each pair
        - buy_prices: A [list] of buy prices for each pair
        - sell_dates: A [list] of sell dates for each pair
        - sell_prices: A [list] of sell prices for each pair
        - state: A [DataFrame] containing the portfolio states
"""
portfolio_series, trades = strategy_test.portfolio_strategy()
portfolio_states_df = trades['state']

In [102]:
def drawdown_analysis(portfolio_curve):
    # --------------------------
    # Drawdown calculation
    # --------------------------
    def calculate_drawdowns(portfolio_curve, threshold=-0.10):
        # calculate cumulative max value
        cum_max = portfolio_curve.cummax()
        # calculate drawdown
        drawdown = (portfolio_curve - cum_max) / cum_max
        
        # initialize variables
        drawdown_ranges = []
        in_drawdown = False  # whether in a drawdown period or not
        start_date = None
        max_dd_in_range = 0  # maximum drawdown in the current range

        # iterate over the drawdown series
        for date, dd in drawdown.items():
            if dd < 0 and not in_drawdown:
                # start of a new drawdown period
                in_drawdown = True
                start_date = date
                max_dd_in_range = dd  # initialize max_dd_in_range
            elif dd < 0 and in_drawdown:
                # update max_dd_in_range
                max_dd_in_range = min(max_dd_in_range, dd)
            elif dd == 0 and in_drawdown:
                # end of the drawdown period
                in_drawdown = False
                end_date = date
                # if the maximum drawdown in the range is below the threshold
                if max_dd_in_range <= threshold:
                    drawdown_ranges.append((start_date, end_date))
        
        return drawdown, drawdown_ranges
    # calculate all the drawdowns and drawdown ranges with depth > threshold

    drawdown, drawdown_ranges = calculate_drawdowns(portfolio_curve)

    # --------------------------
    # plot the drawdown analysis
    # --------------------------
    fig = go.Figure()

    # plot portfolio curve
    fig.add_trace(
        go.Scatter(
            x=portfolio_curve.index,
            y=portfolio_curve.values,
            mode="lines",
            line=dict(color="lightgray", width=2),
            name="Portfolio Value",
            hoverinfo="x+y",
        )
    )

    # plot drawdown ranges
    for start_date, end_date in drawdown_ranges:
        drawdown_range = portfolio_curve.loc[start_date:end_date]
        fig.add_trace(
            go.Scatter(
                x=drawdown_range.index,
                y=drawdown_range.values,
                mode="lines",
                line=dict(color="red", width=2),
                name="Drawdown",
                hoverinfo="x+y",
                fill="tonexty",
                fillcolor="rgba(255,0,0,0.2)",  # fill color with opacity
                showlegend=False,
            )
        )

    # update layout
    fig.update_layout(
        title="Portfolio Drawdown Analysis (>10% Drawdown Periods)",
        xaxis=dict(title="Date"),
        yaxis=dict(title="Portfolio Value"),
        template="plotly_white",
        showlegend=True
    )
   
    fig.show()

def volatility_analysis(portfolio_curve):
    # calculate daily returns
    returns = np.log(portfolio_curve / portfolio_curve.shift(1)).dropna()

    # calculate daily and annualized volatility
    daily_volatility = returns.std()
    annualized_volatility = daily_volatility * np.sqrt(252)
    print(f"Annualized Volatility: {annualized_volatility:.4f}")

    # plot portfolio daily returns
    fig_returns = go.Figure()
    fig_returns.add_trace(
        go.Scatter(
            x=returns.index,
            y=returns,
            mode="lines",
            name="Portfolio Returns",
            line=dict(color="blue", width=1),
        )
    )
    fig_returns.update_layout(
        title="Portfolio Daily Returns",
        xaxis_title="Date",
        yaxis_title="Returns",
        template="plotly_white",
    )
    
    fig_returns.show()

    # calculate 30-day rolling volatility
    rolling_volatility = returns.rolling(window=30).std() * np.sqrt(252)

    # plot 30-day rolling annualized volatility
    fig_volatility = go.Figure()
    fig_volatility.add_trace(
        go.Scatter(
            x=rolling_volatility.index,
            y=rolling_volatility,
            mode="lines",
            name="30-Day Rolling Volatility",
            line=dict(color="red", width=2),
        )
    )
    fig_volatility.update_layout(
        title="30-Day Rolling Annualized Volatility",
        xaxis_title="Date",
        yaxis_title="Volatility",
        template="plotly_white",
    )
   
    fig_volatility.show()

drawdown_analysis(portfolio_series['portfolio'])
volatility_analysis(portfolio_series['portfolio'])

Annualized Volatility: 0.0584


In [ ]:
def calculate_accumulated_trades(trades):
    """
    Input: trades dictionary with [sell dates] as keywords for each pair
    Output: DataFrame with accumulated number of trades for each pair
    """
    accumulated = {}
    for stock in trades:
        if stock == 'state':
            continue
        sell_dates = trades[stock]['sell_dates']
        if not sell_dates:
            accumulated[stock] = pd.Series()
            continue
        # Create a Series with 1s for each sell date
        s = pd.Series(1, index=pd.to_datetime(sell_dates))
        # Resample to daily frequency, sum occurrences, and compute cumulative sum
        s = s.resample('D').sum().cumsum()
        accumulated[stock] = s
    # Combine all series into a DataFrame
    df = pd.concat(accumulated.values(), axis=1, keys=accumulated.keys())
    df.fillna(method='ffill', inplace=True)
    df.fillna(0, inplace=True)
    return df

def plot_accumulated_trades(trades):

    df = calculate_accumulated_trades(trades)
    fig = go.Figure()
    for stock in df.columns:
        fig.add_trace(go.Scatter(
            x=df.index,
            y=df[stock],
            mode='lines',
            name=stock,
            line=dict(width=2)
        ))
    # Update layout for white background and aesthetics
    fig.update_layout(
        title='Accumulated Number of Trades by Pair',
        xaxis_title='Date',
        yaxis_title='Accumulated Trades',
        template='plotly_white',
        legend_title='Pairs',
        width=1400,
        height=600,
        hovermode='x unified'
    )

    fig.show()


def calculate_average_holding_period(entry_times_dict, exit_times_dict):
    """
    Calculate the average holding period for each trade for all pairs.
    """
    holding_periods_dict = {}
    average_holding_period_dict = {}
    
    for stock in entry_times_dict:
        entry_times = entry_times_dict[stock]
        exit_times = exit_times_dict[stock]
        holding_periods = [(exit - entry).days for entry, exit in zip(entry_times, exit_times)]
        average_holding_period = sum(holding_periods) / len(holding_periods) if holding_periods else 0
        holding_periods_dict[stock] = holding_periods
        average_holding_period_dict[stock] = average_holding_period
    
    return holding_periods_dict, average_holding_period_dict

def plot_average_holding_period(holding_periods_dict):
    """
    Plot the average holding period for all pairs.
    """
    
    fig = make_subplots(rows=len(holding_periods_dict), cols=1, shared_xaxes=True)

    for i, (stock, holding_periods) in enumerate(holding_periods_dict.items(), start=1):
        fig.add_trace(
            go.Scatter(x=list(range(len(holding_periods))), 
                    y=holding_periods, 
                    mode='lines+markers',
                    name=f'{stock} Holding Period (days)'),
                    # marker=dict(size=holding_periods),
            row=i, col=1
        )

    fig.update_layout(
        title="Average Holding Period for Trades",
        xaxis_title="Trade Index",
        yaxis_title="Holding Period (days)",
        template="plotly_white",
        height=300 * len(holding_periods_dict),
        width=1200
    )
    fig.update_yaxes(range=[0, 100])
    
    fig.show()


def calculate_mean_return(instrument_series, trades, forex_data):
    """
    Calculate the average daily market return for each trading pair and the average trading return of the strategy.

    Parameters:
      instrument_series: dict, contains a 'portfolio' key, whose index defines the backtest date range.
      trades: dict, contains trading records for each trading pair. The key is the trading pair name, 
              and the value is a dictionary containing 'buy_prices' and 'sell_prices' lists 
              (as well as 'buy_dates' and 'sell_dates').
      forex_data: MultiIndex DataFrame, the first level is 'Close', and the second level is the trading pair name, 
                  storing historical closing price data for each trading pair.

    Returns:
      market_returns: dict, the average daily market return (percentage) for each trading pair during the backtest period.
      mean_returns: dict, the average trading return (percentage) of the strategy for each trading pair.
    """
    start_date = instrument_series['portfolio'].index[0]
    end_date = instrument_series['portfolio'].index[-1]
    
    market_returns = {}
    for inst in forex_data['Close'].columns:
        price_series = forex_data['Close'][inst].loc[start_date:end_date]
        market_returns[inst] = price_series.pct_change().mean() * 100  # 转换为百分比
        
    mean_returns = {}
    for inst in trades:
        if inst == 'state':
            continue
        buy_prices = trades[inst]['buy_prices']
        sell_prices = trades[inst]['sell_prices']

        if len(buy_prices) == 0 or len(sell_prices) == 0:
            mean_returns[inst] = 0
            continue

        returns = [(sell - buy) / buy for buy, sell in zip(buy_prices, sell_prices)]
        mean_returns[inst] = np.mean(returns) * 100  # 转换为百分比
        
    return market_returns, mean_returns

def plot_mean_return(stock_returns,mean_returns):
    """
    Plot the mean return of all trades for each stock.
    """
    fig = go.Figure()
    fig.add_trace(go.Bar(
        x=list(mean_returns.keys()),
        y=list(mean_returns.values()),
        text=[f'{ret:.2f}%' for ret in mean_returns.values()],
        textposition='auto',
        textangle=0,
        name='Mean Return of Strategy (%)'
    ))
    fig.add_trace(go.Bar(
        x=list(stock_returns.keys()),
        y=list(stock_returns.values()),
        text=[f'{ret:.2f}%' for ret in stock_returns.values()],
        textposition='auto',
        name ='Mean Return in History (%)'
    ))
    fig.update_layout(
        title='Mean Return of All Trades by Stock',
        xaxis_title='Stock',
        yaxis_title='Mean Return (%)',
        template='plotly_white',
        width=800,
        height=400
    )
   
    fig.show()


def calculate_trade_statistics(trades):
    """
    Calculate the number and percentage of winning and losing trades,
    as well as the average return of winners and losers.
    """
    trade_stats = {}
    for stock in trades:
        if stock == 'state':
            continue
        buy_prices = trades[stock]['buy_prices']
        sell_prices = trades[stock]['sell_prices']
        if len(buy_prices) == 0 or len(sell_prices) == 0:
            trade_stats[stock] = {
                'winning_trades': 0,
                'losing_trades': 0,
                'winning_percentage': 0,
                'losing_percentage': 0,
                'average_winning_return': 0,
                'average_losing_return': 0
            }
            continue
        
        returns = [(sell - buy) / buy for buy, sell in zip(buy_prices, sell_prices)]
        winning_trades = [ret for ret in returns if ret > 0]
        losing_trades = [ret for ret in returns if ret <= 0]
        
        num_winning_trades = len(winning_trades)
        num_losing_trades = len(losing_trades)
        total_trades = num_winning_trades + num_losing_trades
        
        winning_percentage = (num_winning_trades / total_trades) * 100 if total_trades > 0 else 0
        losing_percentage = (num_losing_trades / total_trades) * 100 if total_trades > 0 else 0
        
        average_winning_return = np.mean(winning_trades) * 100 if winning_trades else 0
        average_losing_return = np.mean(losing_trades) * 100 if losing_trades else 0
        
        trade_stats[stock] = {
            'winning_trades': num_winning_trades,
            'losing_trades': num_losing_trades,
            'winning_percentage': winning_percentage,
            'losing_percentage': losing_percentage,
            'average_winning_return': average_winning_return,
            'average_losing_return': average_losing_return
        }
    
    return trade_stats

def plot_trade_statistics(trade_stats):
    """
    Plot the number and percentage of winning and losing trades,
    as well as the average return of winners vs. losers.
    """
    stocks = list(trade_stats.keys())
    winning_trades = [trade_stats[stock]['winning_trades'] for stock in stocks]
    losing_trades = [trade_stats[stock]['losing_trades'] for stock in stocks]
    winning_percentage = [trade_stats[stock]['winning_percentage'] for stock in stocks]
    losing_percentage = [trade_stats[stock]['losing_percentage'] for stock in stocks]
    average_winning_return = [trade_stats[stock]['average_winning_return'] for stock in stocks]
    average_losing_return = [trade_stats[stock]['average_losing_return'] for stock in stocks]
    
    fig = make_subplots(rows=3, cols=1, shared_xaxes=True, vertical_spacing=0.1,
                        subplot_titles=('Number of Winning and Losing Trades', 'Average Return of Winners vs. Losers', 'Percentage of Winning and Losing Trades'))
    
    # Number of winning and losing trades
    fig.add_trace(go.Bar(x=stocks, y=winning_trades, name='Winning Trades', marker_color='green'), row=1, col=1)
    fig.add_trace(go.Bar(x=stocks, y=losing_trades, name='Losing Trades', marker_color='red'), row=1, col=1)
    
    # Average return of winners vs. losers
    fig.add_trace(go.Bar(x=stocks, y=average_winning_return, name='Average Winning Return (%)', marker_color='green'), row=2, col=1)
    fig.add_trace(go.Bar(x=stocks, y=average_losing_return, name='Average Losing Return (%)', marker_color='red'), row=2, col=1)

    # Percentage of winning and losing trades
    fig.add_trace(go.Bar(x=stocks, y=winning_percentage, name='Winning Trades (%)', marker_color='green'), row=3, col=1)
    fig.add_trace(go.Bar(x=stocks, y=losing_percentage, name='Losing Trades (%)', marker_color='red'), row=3, col=1)
    
    fig.update_layout(
        title='Winning & Losing Trades Breakdown',
        xaxis_title='Pairs',
        yaxis_title='Number of Trades',
        yaxis2_title='Average Return (%)',
        yaxis3_title='Percentage of Trades (%)',
        template='plotly_white',
        height=800,
        width=1000,
        legend=dict(x=1.02, y=1, xanchor='left', yanchor='top')
    )
    
    fig.show()


def calculate_monthly_yearly_returns(series):
    """
    Calculate monthly and yearly returns from the portfolio series.
    """
    series['portfolio'] = series['portfolio'][~series['portfolio'].index.duplicated(keep='first')]
    
    # Ensure at least one data point per month/year before computing returns
    monthly_prices = series['portfolio'].resample('M').last()
    yearly_prices = series['portfolio'].resample('Y').last()

    # Compute percentage changes only where valid
    monthly_returns = monthly_prices.pct_change()
    yearly_returns = yearly_prices.pct_change()

    # Adjust first-year return calculation
    first_year_return = (yearly_prices.iloc[0] - series['portfolio'].iloc[0]) / series['portfolio'].iloc[0]
    first_month = series['portfolio'].index[0].month
    yearly_returns.iloc[0] = first_year_return * 12 / (12 - first_month + 1) # Adjust for partial year

    return monthly_returns, yearly_returns

def plot_monthly_yearly_performance(monthly_returns, yearly_returns):
    """
    Plot the monthly and yearly performance using bar charts and heatmaps.
    """
    # Plot monthly returns as a bar chart
    fig = px.bar(monthly_returns, title='Monthly Returns', labels={'index': 'Month', 'value': 'Return'})
    fig.update_layout(xaxis_title='Month', yaxis_title='Return', xaxis_tickformat='%b %Y', showlegend=False)
   
    fig.show()

    # Plot yearly returns as a bar chart
    fig = px.bar(yearly_returns, title='Yearly Returns', labels={'index': 'Year', 'value': 'Return'})
    fig.update_layout(
        xaxis_title='Year', 
        yaxis_title='Return', 
        xaxis_tickformat='%Y', 
        showlegend=False,
        xaxis=dict(
            tickmode='array',
            tickvals=yearly_returns.index,
            ticktext=[str(year.year) for year in yearly_returns.index]
        )
    )
   
    fig.show()

    # Create a heatmap for monthly returns
    monthly_returns_df = monthly_returns.to_frame(name='Return')
    monthly_returns_df['Year'] = monthly_returns_df.index.year
    monthly_returns_df['Month'] = monthly_returns_df.index.month
    monthly_returns_pivot = monthly_returns_df.pivot(index='Year', columns='Month', values='Return').fillna(0)

    fig = go.Figure(data=go.Heatmap(
        z=monthly_returns_pivot.values,
        x=monthly_returns_pivot.columns,
        y=monthly_returns_pivot.index,
        colorscale='Viridis',
        colorbar=dict(title='Return')
    ))
    fig.update_layout(title='Monthly Returns Heatmap', xaxis_title='Month', yaxis_title='Year')
    
    fig.show()

def calculate_position_allocation(portfolio_states_df, data, stocks):
    allocation_df = portfolio_states_df[stocks].copy()
    for stock in stocks:
        allocation_df[stock] = allocation_df[stock] * data['Close'][stock].loc[allocation_df.index]
    allocation_df['Cash'] = portfolio_states_df['cash']
    return allocation_df

def plot_position_discount_stacked_chart(allocation_df):
    fig = go.Figure()
    # Add each stock's allocation
    for stock in allocation_df.columns:
        if stock == 'Cash':
            continue  # Handle Cash separately
        fig.add_trace(go.Scatter(
            x=allocation_df.index,
            y=allocation_df[stock],
            mode='lines',
            stackgroup='one',
            name=stock
        ))
    # Add Cash allocation
    fig.add_trace(go.Scatter(
        x=allocation_df.index,
        y=allocation_df['Cash'],
        mode='lines',
        stackgroup='one',
        name='Cash',
        line=dict(color='green', width=2)
    ))
    fig.update_layout(
        title='Position Allocation Over Time',
        xaxis_title='Date',
        yaxis_title='Value',
        template='plotly_white',
        width=1400,
        height=600
    )
   
    fig.show()
def plot_position_proportional(allocation_df):
    # Convert absolute values to percentages
    proportional = allocation_df.div(allocation_df.sum(axis=1), axis=0)
    
    fig = px.area(
        proportional,
        title="Proportional Position Allocation",
        labels={"value": "Percentage Allocation"}
    )
    fig.update_layout(yaxis_tickformat=".0%")
    
    fig.show()


def plot_heatmap(allocation_df):
    # Filter small allocations (<5%)
    total = allocation_df.sum(axis=1)
    filtered = allocation_df[allocation_df.div(total, axis=0) > 0.05]
    
    fig = px.imshow(
        filtered.T,
        labels=dict(x="Date", y="Asset"),
        aspect="auto",
        title="Significant Holdings Heatmap (>5% allocation)"
    )
    fig.update_xaxes(tickangle=45)
   
    fig.show() 


In [94]:
# ------------------- Visualization Output from portfolio_series & trades------------------- #

# Extract all entry and exit times from the trades dictionary
all_entry_times = dict()
for stock in trades:
    if stock == 'state':
        continue
    all_entry_times[stock] = trades[stock]['buy_dates']

all_exit_times = dict()
for stock in trades:
    if stock == 'state':
        continue
    all_exit_times[stock] = trades[stock]['sell_dates']

In [95]:
plot_accumulated_trades(trades)

In [96]:
# Calculate holding periods and average holding period
holding_periods_dict, average_holding_period_dict = calculate_average_holding_period(all_entry_times, all_exit_times)
plot_average_holding_period(holding_periods_dict)

In [97]:
# Calculate mean returns
stock_returns, mean_returns = calculate_mean_return(portfolio_series, trades,forex_data)
# Plot mean returns
plot_mean_return(stock_returns, mean_returns)




In [98]:
# Calculate trade statistics
trade_stats = calculate_trade_statistics(trades)
# Plot trade statistics
plot_trade_statistics(trade_stats)


In [99]:
# Calculate monthly and yearly returns
monthly_returns, yearly_returns = calculate_monthly_yearly_returns(portfolio_series)
# Plot the performance
plot_monthly_yearly_performance(monthly_returns, yearly_returns)




In [100]:
# Calculate correct allocation
allocation_df = calculate_position_allocation(portfolio_states_df, forex_data, forex_pairs)

# Verify total matches portfolio series
total_allocation = allocation_df.sum(axis=1)
print("Final allocation total:", total_allocation.iloc[-1])
print("Portfolio series final value:", portfolio_series['portfolio'].iloc[-1])


# Plot corrected chart
plot_position_discount_stacked_chart(allocation_df)
# Plot proportional allocation
plot_position_proportional(allocation_df)
# Plot heatmap
plot_heatmap(allocation_df)

Final allocation total: 10016.363619484471
Portfolio series final value: 10016.363619484471


In [101]:
def trade_distribution_analysis(portfolio_curve):
    # calculate daily, weekly and monthly returns
    daily_return = portfolio_curve.pct_change()
    weekly_return = portfolio_curve.resample('W').ffill().pct_change()
    monthly_return = portfolio_curve.resample('M').ffill().pct_change()

    # calculate rolling returns
    rolling_windows = [3, 6, 12]  # 3-month, 6-month, and 12-month rolling returns
    rolling_returns = {
        f"RollingReturn_{window}M": portfolio_curve.pct_change(periods=window * 21)  # 21 trading days per month
        for window in rolling_windows
    }

    analysis_df = pd.DataFrame({
        "NetValue": portfolio_curve,
        "DailyReturn": daily_return,
        "WeeklyReturn": weekly_return,
        "MonthlyReturn": monthly_return,
        **rolling_returns
    })

    # add a column to indicate gain or loss
    analysis_df["GainLoss"] = analysis_df["DailyReturn"] > 0

    # ------------------
    # plot the daily, weekly and monthly return distributions
    # ------------------

    # daily return distribution
    daily_return_fig = px.histogram(
        analysis_df,
        x="DailyReturn",
        nbins=50,
        marginal="box",  # add box plot
        title="Daily Return Distribution",
        labels={"DailyReturn": "Daily Return"},
        color_discrete_sequence=["blue"]
    )
    daily_return_fig.update_layout(bargap=0.1)

    # weekly return distribution
    weekly_return_fig = px.histogram(
        analysis_df,
        x="WeeklyReturn",
        nbins=50,
        marginal="box",  # add box plot
        title="Weekly Return Distribution",
        labels={"WeeklyReturn": "Weekly Return"},
        color_discrete_sequence=["green"]
    )
    weekly_return_fig.update_layout(bargap=0.1)

    # monthly return distribution
    monthly_return_fig = px.histogram(
        analysis_df,
        x="MonthlyReturn",
        nbins=50,
        marginal="box",  # add box plot
        title="Monthly Return Distribution",
        labels={"MonthlyReturn": "Monthly Return"},
        color_discrete_sequence=["purple"]
    )
    monthly_return_fig.update_layout(bargap=0.1)

    # ------------------
    # plot the gain/loss histogram
    # ------------------

    # histogram of daily returns with gain/loss color coding
    gain_loss_fig = px.histogram(
        analysis_df,
        x="DailyReturn",
        nbins=50,
        title="Histogram of Returns (Gain/Loss)",
        labels={"DailyReturn": "Daily Return"},
        color="GainLoss",  # color by GainLoss column
        color_discrete_map={True: "green", False: "red"}
    )
    gain_loss_fig.update_layout(bargap=0.1)
    gain_loss_fig.add_vline(x=0, line_width=2, line_dash="dash", line_color="black", annotation_text="Break-Even")

    # ------------------
    # plot the rolling return analysis
    # ------------------

    # plot rolling returns for different windows
    rolling_return_fig = go.Figure()

    for window in rolling_windows:
        rolling_return_fig.add_trace(
            go.Scatter(
                x=analysis_df.index,
                y=analysis_df[f"RollingReturn_{window}M"],
                mode='lines',
                name=f'{window}-Month Rolling Return'
            )
        )

    # add break-even line
    rolling_return_fig.add_hline(y=0, line_dash="dot", line_color="red", annotation_text="Break-Even")

    rolling_return_fig.update_layout(
        title="Rolling Return Analysis",
        xaxis_title="Date",
        yaxis_title="Rolling Return",
        legend_title="Rolling Window",
        template="plotly_white"
    )

    # ------------------
    # Display the figures
    # ------------------

    # show daily, weekly and monthly return distributions
    # daily_return_fig.write_image("./Strategy1/daily_return_2.pdf", engine="kaleido")
    # weekly_return_fig.write_image("./Strategy1/weekly_return_2.pdf", engine="kaleido")
    # monthly_return_fig.write_image("./Strategy1/monthly_return_2.pdf", engine="kaleido")
    # rolling_return_fig.write_image("./Strategy1/rolling_return_2.pdf", engine="kaleido")
    # gain_loss_fig.write_image("./Strategy1/gain_loss_2.pdf", engine="kaleido")
    
    daily_return_fig.show()
    weekly_return_fig.show()
    monthly_return_fig.show()

    # show gain/loss histogram
    gain_loss_fig.show()

    # show rolling return analysis
    rolling_return_fig.show()

trade_distribution_analysis(portfolio_series['portfolio'])